<a href="https://colab.research.google.com/github/kumarrishav4/3d_model_visualizer/blob/main/3d_visualizer.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# 3d visualizer


In [ ]:
!pip install trimesh plotly ipywidgets

In [ ]:
import trimesh
import plotly.graph_objects as go

In [ ]:
import ipywidgets as widgets
from IPython.display import display
import trimesh
import io

# Create a global variable to hold the mesh
uploaded_mesh = None

# Create an upload button widget
upload_widget = widgets.FileUpload(
    accept='.stl',  # Only .stl files
    multiple=False  # Disable multiple file upload
)

# Function to handle file upload
def handle_upload(change):
    global uploaded_mesh  # Access the global variable
    # Load the uploaded STL file
    uploaded_file = upload_widget.value
    if uploaded_file:
        for name, file_info in uploaded_file.items():
            stl_data = file_info['content']  # File content in bytes
            file_like_object = io.BytesIO(stl_data)  # Convert bytes to file-like object
            uploaded_mesh = trimesh.load_mesh(file_like_object, file_type='stl')  # Load STL using trimesh
            print(f"Uploaded: {name}")
            print(f"Mesh loaded with {len(uploaded_mesh.vertices)} vertices and {len(uploaded_mesh.faces)} faces")

# Attach the handler function to the upload widget
upload_widget.observe(handle_upload, names='value')

# Display the upload button
display(upload_widget)


FileUpload(value={}, accept='.stl', description='Upload')

Uploaded: finger.stl
Mesh loaded with 1700 vertices and 3459 faces


In [ ]:
mesh = uploaded_mesh

In [ ]:
# Extract vertices and faces
x, y, z = mesh.vertices.T
faces = mesh.faces

# Create solid mesh
solid_mesh = go.Mesh3d(x=x, y=y, z=z, i=faces[:, 0], j=faces[:, 1], k=faces[:, 2], color='lightblue', opacity=1)

# Create edges for wireframe visualization
edges = mesh.edges
wireframe_x = []
wireframe_y = []
wireframe_z = []

for edge in edges:
    wireframe_x.extend([mesh.vertices[edge[0]][0], mesh.vertices[edge[1]][0], None])  # None to break the line
    wireframe_y.extend([mesh.vertices[edge[0]][1], mesh.vertices[edge[1]][1], None])
    wireframe_z.extend([mesh.vertices[edge[0]][2], mesh.vertices[edge[1]][2], None])

# Create wireframe mesh
wireframe_mesh = go.Scatter3d(x=wireframe_x, y=wireframe_y, z=wireframe_z, mode='lines', line=dict(color='black', width=2))

# Create textured mesh (just using a different color for demonstration)
textured_mesh = go.Mesh3d(x=x, y=y, z=z, i=faces[:, 0], j=faces[:, 1], k=faces[:, 2], color='lightgreen', opacity=0.5)

# Create a figure with solid view initially
fig = go.Figure(data=[solid_mesh])  # Start with solid mesh

# Add buttons to switch between views
fig.update_layout(
    updatemenus=[
        dict(
            type="buttons",
            showactive=True,
            buttons=[
                dict(label="Solid",
                     method="update",
                     args=[{"visible": [True, True, False]},
                           {"title": "3D View - Solid Mode"}]),
                dict(label="Wireframe",
                     method="update",
                     args=[{"visible": [False, True, False]},
                           {"title": "3D View - Wireframe Mode"}]),
                dict(label="Textured",
                     method="update",
                     args=[{"visible": [False, True, True]},
                           {"title": "3D View - Textured Mode"}])
            ],
        )
    ]
)

# Add traces for wireframe and textured (initially hidden)
fig.add_trace(wireframe_mesh)  # Wireframe (initially hidden)
fig.add_trace(textured_mesh)   # Textured (initially hidden)

# Set the visibility so that solid is always shown when switched back
solid_mesh.visible = True
wireframe_mesh.visible = False
textured_mesh.visible = False

# Show the figure in Colab
fig.show()


In [ ]:



# Extract vertices and faces
x, y, z = mesh.vertices.T
faces = mesh.faces

# Create solid mesh (faces)
solid_mesh = go.Mesh3d(x=x, y=y, z=z, i=faces[:, 0], j=faces[:, 1], k=faces[:, 2], color='lightblue', opacity=1, name="Faces")

# Create edges for wireframe visualization (edges)
edges = mesh.edges
wireframe_x = []
wireframe_y = []
wireframe_z = []

for edge in edges:
    wireframe_x.extend([mesh.vertices[edge[0]][0], mesh.vertices[edge[1]][0], None])  # None to break the line
    wireframe_y.extend([mesh.vertices[edge[0]][1], mesh.vertices[edge[1]][1], None])
    wireframe_z.extend([mesh.vertices[edge[0]][2], mesh.vertices[edge[1]][2], None])

# Create wireframe mesh (edges)
wireframe_mesh = go.Scatter3d(x=wireframe_x, y=wireframe_y, z=wireframe_z, mode='lines', line=dict(color='black', width=2), name="Edges")

# Create a scatter plot for the vertices
vertex_mesh = go.Scatter3d(x=x, y=y, z=z, mode='markers', marker=dict(color='red', size=3), name="Vertices")

# Create semi-transparent face mesh for "Point View"
face_with_opacity = go.Mesh3d(x=x, y=y, z=z, i=faces[:, 0], j=faces[:, 1], k=faces[:, 2], color='lightblue', opacity=0.5, name="Faces with 50% Opacity")

# Create a figure with nothing shown initially
fig = go.Figure()

# Add traces for solid (faces), wireframe (edges), and vertices (initially hidden)
fig.add_trace(solid_mesh)
fig.add_trace(wireframe_mesh)
fig.add_trace(vertex_mesh)
fig.add_trace(face_with_opacity)

# Set all traces as invisible by default
solid_mesh.visible = False
wireframe_mesh.visible = False
vertex_mesh.visible = False
face_with_opacity.visible = False

# Add buttons to switch between views and toggle components (vertices, edges, faces)
fig.update_layout(
    updatemenus=[
        dict(
            type="buttons",
            showactive=True,
            buttons=[
                # Show only faces
                dict(label="Show Faces",
                     method="update",
                     args=[{"visible": [True, False, False, False]},
                           {"title": "3D View - Show Faces"}]),

                # Show only edges
                dict(label="Show Edges",
                     method="update",
                     args=[{"visible": [False, True, False, False]},
                           {"title": "3D View - Show Edges"}]),

                # Show only vertices
                dict(label="Show Vertices",
                     method="update",
                     args=[{"visible": [False, False, True, False]},
                           {"title": "3D View - Show Vertices"}]),

                # Solid Mode (Faces + Edges)
                dict(label="Solid",
                     method="update",
                     args=[{"visible": [True, True, False, False]},
                           {"title": "3D View - Solid Mode (Faces + Edges)"}]),

                # Wireframe Mode (Edges + Vertices)
                dict(label="Wireframe",
                     method="update",
                     args=[{"visible": [False, True, True, False]},
                           {"title": "3D View - Wireframe Mode (Edges + Vertices)"}]),

                # Point View (Faces with 50% opacity + Vertices)
                dict(label="Point View",
                     method="update",
                     args=[{"visible": [False, False, True, True]},
                           {"title": "3D View - Point View (Faces with 50% Opacity + Vertices)"}])
            ],
        )
    ]
)

# Show the figure in Colab
fig.show()


In [ ]:


# Extract vertices and faces
x, y, z = mesh.vertices.T
faces = mesh.faces

# Create solid mesh (faces)
solid_mesh = go.Mesh3d(x=x, y=y, z=z, i=faces[:, 0], j=faces[:, 1], k=faces[:, 2], color='lightblue', opacity=1, name="Faces")

# Create edges for wireframe visualization (edges)
edges = mesh.edges
wireframe_x = []
wireframe_y = []
wireframe_z = []

for edge in edges:
    wireframe_x.extend([mesh.vertices[edge[0]][0], mesh.vertices[edge[1]][0], None])  # None to break the line
    wireframe_y.extend([mesh.vertices[edge[0]][1], mesh.vertices[edge[1]][1], None])
    wireframe_z.extend([mesh.vertices[edge[0]][2], mesh.vertices[edge[1]][2], None])

# Create wireframe mesh (edges)
wireframe_mesh = go.Scatter3d(x=wireframe_x, y=wireframe_y, z=wireframe_z, mode='lines', line=dict(color='black', width=2), name="Edges")

# Create a scatter plot for the vertices
vertex_mesh = go.Scatter3d(x=x, y=y, z=z, mode='markers', marker=dict(color='red', size=3), name="Vertices")

# Create semi-transparent face mesh for "Point View"
face_with_opacity = go.Mesh3d(x=x, y=y, z=z, i=faces[:, 0], j=faces[:, 1], k=faces[:, 2], color='lightblue', opacity=0.5, name="Faces with 50% Opacity")

# Create a figure with nothing shown initially
fig = go.Figure()

# Add traces for solid (faces), wireframe (edges), and vertices (initially hidden)
fig.add_trace(solid_mesh)
fig.add_trace(wireframe_mesh)
fig.add_trace(vertex_mesh)
fig.add_trace(face_with_opacity)

# Set all traces as invisible by default
solid_mesh.visible = False
wireframe_mesh.visible = False
vertex_mesh.visible = False
face_with_opacity.visible = False

# Add buttons to switch between views and toggle components (vertices, edges, faces)
fig.update_layout(
    updatemenus=[
        # First set of buttons on the left (toggling individual components)
        dict(
            type="buttons",
            direction="down",
            showactive=True,
            buttons=[
                dict(label="Show Faces",
                     method="update",
                     args=[{"visible": [True, False, False, False]},
                           {"title": "3D View - Show Faces"}]),

                dict(label="Show Edges",
                     method="update",
                     args=[{"visible": [False, True, False, False]},
                           {"title": "3D View - Show Edges"}]),

                dict(label="Show Vertices",
                     method="update",
                     args=[{"visible": [False, False, True, False]},
                           {"title": "3D View - Show Vertices"}]),
            ],
            pad={"r": 10, "t": 10},
            x=0,  # Position the buttons to the far left
            xanchor="left",
            y=0.9,
            yanchor="top"
        ),

        # Second set of buttons on the right (switching between modes)
        dict(
            type="buttons",
            direction="down",
            showactive=True,
            buttons=[
                dict(label="Solid",
                     method="update",
                     args=[{"visible": [True, True, False, False]},
                           {"title": "3D View - Solid Mode (Faces + Edges)"}]),

                dict(label="Wireframe",
                     method="update",
                     args=[{"visible": [False, True, True, False]},
                           {"title": "3D View - Wireframe Mode (Edges + Vertices)"}]),

                dict(label="Point View",
                     method="update",
                     args=[{"visible": [False, False, True, True]},
                           {"title": "3D View - Point View (Faces with 50% Opacity + Vertices)"}]),
            ],
            pad={"r": 10, "t": 10},
            x=1,  # Position the buttons to the far right
            xanchor="right",
            y=0.9,
            yanchor="top"
        )
    ]
)

# Show the figure in Colab
fig.show()
